In [1]:
%%capture
!pip install pytorch-lightning
!pip install lightning-bolts

# Data preparation

In [2]:
from torchvision import models
import torch
import torchvision
import torchvision.transforms as transforms
from torch.utils.data import DataLoader
from torch.optim import Adam
from torch.nn.functional import cross_entropy

from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
import pytorch_lightning as pl
import torch
from torch.utils.data import random_split, DataLoader, Subset
from torchvision import transforms
import numpy as np

from pl_bolts.models.self_supervised.swav.transforms import SwAVEvalDataTransform, SwAVTrainDataTransform

#parameters
data_dir =  '/content/drive/MyDrive/NN/datasets'
num_classes=3
batch_size=16
train_ratio=0.77
seed = 1

#transformations
train_transform = transforms.Compose(
            [transforms.Resize((224,224)),
             transforms.ToTensor(),
             transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
             ])
   
#transformations
val_transform = transforms.Compose(
            [transforms.Resize((224,224)),
             transforms.ToTensor(),
             transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
             ])


#Set for SwAV
# #image augmentation parameters
# normalization = transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
# size_crops = [224, 96]
# nmb_crops = [2, 6]
# min_scale_crops = [0.14, 0.05]
# max_scale_crops = [1.0, 0.14]
# gaussian_blur = True
# jitter_strength = 1.0


# #transformations
# train_transform = SwAVTrainDataTransform(
#         normalize=normalization,
#         size_crops=size_crops,
#         nmb_crops=nmb_crops,
#         min_scale_crops=min_scale_crops,
#         max_scale_crops=max_scale_crops,
#         gaussian_blur=gaussian_blur,
#         jitter_strength=jitter_strength
#         )
   
# #transformations
# val_transform = SwAVEvalDataTransform(
#         normalize=normalization,
#         size_crops=size_crops,
#         nmb_crops=nmb_crops,
#         min_scale_crops=min_scale_crops,
#         max_scale_crops=max_scale_crops,
#         gaussian_blur=gaussian_blur,
#         jitter_strength=jitter_strength
#         )

#load data
data_full = torchvision.datasets.ImageFolder(root=data_dir,  transform=train_transform)
train_dataset = torchvision.datasets.ImageFolder(root=data_dir, transform=train_transform)
val_dataset = torchvision.datasets.ImageFolder(root=data_dir, transform=val_transform)


#split dataset
num_samples = len(train_dataset)
idxs = list(range(num_samples))
split = int(train_ratio*num_samples)
np.random.seed(seed)
np.random.shuffle(idxs)

train_idx, valid_idx = idxs[:split], idxs[split:]

#Assign train, val, test dataset for use in dataloaders
data_train = Subset(train_dataset, train_idx)
data_val =  Subset(val_dataset, valid_idx)
data_test = torchvision.datasets.ImageFolder(data_dir, transform=train_transform)

#data loaders
train_loader = DataLoader(data_train, batch_size=16, shuffle=True)
val_loader = DataLoader(data_val, batch_size=20, shuffle=False)
test_loader = DataLoader(data_test, batch_size=16, shuffle=False)

In [11]:
for batch in val_loader:
  x, y = batch
  print(y)
  break

tensor([2, 0, 0, 0, 0, 0, 0, 1, 0, 0, 2, 0, 0, 1, 0, 2, 0, 2, 0, 0])


# SwAV loss

In [ ]:
import pytorch_lightning as pl

from pl_bolts.models.self_supervised import SwAV
from pytorch_lightning.metrics.functional import accuracy
from pl_bolts.callbacks.ssl_online import SSLOnlineEvaluator

#parameters
optimizer = "adam"
temperature = 0.1
learning_rate = 1e-3
hidden_mlp = 2048 
feat_dim = 256
num_samples = 84

pts = [9, 15, 30, 100, 500]

for pt in pts:
  nmb_prototypes = pt

  model= SwAV(gpus=1,
      num_samples = num_samples,
      batch_size = batch_size,
      dataset = data_full,
      hidden_mlp = hidden_mlp,
      feat_dim = feat_dim, 
      nmb_prototypes = nmb_prototypes,
      nmb_crops = [2, 6],
      optimizer = optimizer,
      temperature = temperature,
      learning_rate = learning_rate)

  logger = pl.loggers.TensorBoardLogger(name=f'prototypes-{pt}', save_dir='lightning_logs')

  trainer = pl.Trainer(
    max_epochs=10,
    gpus=1,
    logger = logger,
    log_every_n_steps=4,
    )
  
  trainer.fit(model, train_loader, val_loader)

In [ ]:
#tensorboard
%reload_ext tensorboard
%tensorboard --logdir lightning_logs/

# Set SwAV

In [4]:
import pytorch_lightning as pl

from pl_bolts.callbacks.ssl_online import SSLOnlineEvaluator
from pl_bolts.models.self_supervised import SwAV
from pytorch_lightning.metrics.functional import accuracy

#traininig
class SSLImageClassifier(pl.LightningModule):
  def __init__(self,
               num_samples = 64,
               dataset = train_loader,
               lr=1e-3,
               num_prototypes = 3000,
               hidden_mlp = 2048,
               feat_dim = 256,
               num_classes=3,
               nmb_crops = [2, 6]):
    super().__init__()
    self.num_samples = num_samples
    self.num_prototypes = num_prototypes
    self.hidden_mlp = hidden_mlp
    self.feat_dim = feat_dim
    self.num_classes = num_classes
    self.nmb_crops = nmb_crops

    swav= SwAV(gpus=1,
          num_samples = self.num_samples,
          batch_size = 16,
          dataset = train_loader,
          hidden_mlp = self.hidden_mlp, #z features
          feat_dim = self.feat_dim, #output dimension of projection head
          nmb_prototypes = self.num_prototypes,
          nmb_crops = self.nmb_crops
        )

    self.save_hyperparameters()
    self.backbone = swav.model
    self.finetune_layer = torch.nn.Linear(self.num_prototypes, self.num_classes)
  
  def training_step(self, batch, batch_idx):
    x, y = batch
    if self.trainer.current_epoch < 10:
      with torch.no_grad():
        (f1, f2)= self.backbone(x)
        features = f2
    
    else:
      (f1, f2)= self.backbone(x)
      features = f2

    preds = self.finetune_layer(features)
    loss = cross_entropy(preds, y)
    self.log('train_loss', loss)
    self.log('train_acc', accuracy(preds, y))
    return loss

  def validation_step(self, batch, batch_idx):
    x, y = batch
    (f1, f2)= self.backbone(x)
    features = f2
    
    preds = self.finetune_layer(features)
    loss = cross_entropy(preds, y)
    self.log('val_loss', loss)
    self.log('val_acc', accuracy(preds, y))
    return loss

  def configure_optimizers(self):
    optimizer = Adam(self.parameters(), lr=self.hparams.lr)
    return optimizer

# Support Function

In [6]:
import numpy as np
crops= [[2,4], [2,6], [2,8], [2,10]]
crops

[[2, 4], [2, 6], [2, 8], [2, 10]]

In [7]:
num_epochs = [150]

# SwAV

In [8]:
from torch.serialization import check_module_version_greater_or_equal

for num_epoch in num_epochs:
  for crop in crops:
    print('SELF-SUPERVISED PRE-TRAINED')
    print('NUM_EPOCHS', num_epoch)
    print('CROPS', crop)

    max_epoch = num_epoch
    val_check_epoch = max_epoch//5
    print('max_epochs: ', max_epoch)
    print('val_epochs: ', val_check_epoch)

    #model
    ssl_classifier = SSLImageClassifier(lr=1e-3, nmb_crops=crop)

    #train
    logger = pl.loggers.TensorBoardLogger(name=f'ssl-{crop}-{num_epoch}', save_dir='lightning_logs')

    trainer = pl.Trainer(progress_bar_refresh_rate=4,
                                gpus=1,
                                max_epochs = max_epoch,
                                logger = logger,
                                log_every_n_steps=4
                                )

    trainer.fit(ssl_classifier, train_loader, val_loader)

SELF-SUPERVISED PRE-TRAINED
NUM_EPOCHS 150
CROPS [2, 4]
max_epochs:  150
val_epochs:  30


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name           | Type   | Params
------------------------------------------
0 | backbone       | ResNet | 29.0 M
1 | finetune_layer | Linear | 9.0 K 
------------------------------------------
29.0 M    Trainable params
0         Non-trainable params
29.0 M    Total params
116.040   Total estimated model params size (MB)


Validation sanity check: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/torch/nn/functional.py:718: UserWarning: Named tensors and all their associated APIs are an experimental feature and subject to change. Please do not use them for anything important until they are released as stable. (Triggered internally at  /pytorch/c10/core/TensorImpl.h:1156.)
  return torch.max_pool2d(input, kernel_size, stride, padding, dilation, ceil_mode)
/usr/local/lib/python3.7/dist-packages/deprecate/deprecation.py:115: LightningDeprecationWarning: The `accuracy` was deprecated since v1.3.0 in favor of `torchmetrics.functional.classification.accuracy.accuracy`. It will be removed in v1.5.0.
  stream(template_mgs % msg_args)


Training: -1it [00:00, ?it/s]

...

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

In [ ]:
#tensorboard
%reload_ext tensorboard
%tensorboard --logdir lightning_logs/

In [13]:
ssl_classifier

SSLImageClassifier(
  (backbone): ResNet(
    (padding): ConstantPad2d(padding=(1, 1, 1, 1), value=0.0)
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(2, 2), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (relu): ReLU(inplace=True)
    (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
    (layer1): Sequential(
      (0): Bottleneck(
        (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
        (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
        (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
     

#Pretrained

In [ ]:
import pytorch_lightning as pl
from pytorch_lightning.metrics.functional import accuracy
from pl_bolts.models.self_supervised import SwAV

#weight_path = 'https://pl-bolts-weights.s3.us-east-2.amazonaws.com/swav/bolts_swav_imagenet/swav_imagenet.ckpt'
swav = SwAV.load_from_checkpoint(weight_path, strict=False, nmb_prototypes=3000)

class SSLImageClassifier(pl.LightningModule):
  def __init__(self, num_classes=3, lr=1e-3):
    super().__init__()
    self.save_hyperparameters()

    self.backbone = swav.model #pretrained model
    self.finetune_layer = torch.nn.Linear(3000, num_classes)
  
  def training_step(self, batch, batch_idx):
    x, y = batch
    if self.trainer.current_epoch < 10:
      with torch.no_grad():
        (f1, f2)= self.backbone(x)
        features = f2
    
    else:
      (f1, f2)= self.backbone(x)
      features = f2

    preds = self.finetune_layer(features)
    loss = cross_entropy(preds, y)
    self.log('train_loss', loss)
    self.log('train_acc', accuracy(preds, y))
    return loss

  def validation_step(self, batch, batch_idx):
    x, y = batch
    (f1, f2)= self.backbone(x)
    features = f2
    
    preds = self.finetune_layer(features)
    loss = cross_entropy(preds, y)
    self.log('val_loss', loss)
    self.log('val_acc', accuracy(preds, y))
    return loss

  def configure_optimizers(self):
    optimizer = Adam(self.parameters(), lr=self.hparams.lr)
    return optimizer

/usr/local/lib/python3.7/dist-packages/pytorch_lightning/core/saving.py:210: UserWarning: Found keys that are not in the model state dict but in the checkpoint: ['non_linear_evaluator.block_forward.2.weight', 'non_linear_evaluator.block_forward.2.bias']
  f"Found keys that are not in the model state dict but in the checkpoint: {keys.unexpected_keys}"
